# Part Section to Layers
Splits part section file into smaller layer files.

In [1]:
import matplotlib.pyplot as plt
import numpy as np
import os
import pickle
import pyarrow as pa
import pyarrow.parquet as pq

from tqdm import tqdm 

In [3]:
CHECK_SHAPE = False

layer_folder = "layer"
layer_table_folder = "layer_table"

# config_folder = "base"
# config_folder = "block"
# config_folder = "overhang_no_supports"
config_folder = "overhang_with_supports"

In [ ]:
non_array = [str, int, np.uint8, np.uint16, np.float64]
for layer_file in tqdm(os.listdir(f"{layer_folder}/{config_folder}")):
    # print(layer_file)
    with open(f"{layer_folder}/{config_folder}/{layer_file}", "rb") as f:
        layer = pickle.load(f)

        pydict = {}
        layer_number = layer["layer_number"]
        for key, value in layer.items():
            if (type(value) in non_array):
                pydict[key] = [value]
            elif (isinstance(value, np.ndarray)):
                # print(key, value.shape, type(value.shape))
                pydict[f"{key}_shape"] = [value.shape]
                pydict[key] = [value.flatten()]
            else:
                print(key, type(value))
        # print(pydict)
        table = pa.Table.from_pydict(pydict)
        pq.write_table(table, f"{layer_table_folder}/{config_folder}/{layer_number}.parquet")
        # print(table)

        if CHECK_SHAPE:
            radiant_temps = layer["radiant_temp"]
            radiant_temps_shape = radiant_temps.shape
            radiant_temps_flat = radiant_temps.flatten()
            radiant_temps_arrow = pa.array(radiant_temps_flat)

            radiant_temps_reshaped = radiant_temps_flat.reshape(radiant_temps_shape)

            # print(radiant_temps_reshaped)
            arrow_radiant_temps_flat = table["radiant_temp"]
            # print("called")
            # print(arrow_radiant_temps_flat[0])
            arrow_radiant_temps_shape = table["radiant_temp_shape"][0]

            # print(arrow_radiant_temps_flat)
            arrow_radiant_temps_reshaped = arrow_radiant_temps_flat.reshape(arrow_radiant_temps_shape)

            plt.imshow(radiant_temps[100])
            plt.show()

            plt.imshow(radiant_temps_reshaped[100])
            plt.show()

            plt.imshow(arrow_radiant_temps_reshaped[100])
            plt.show()


In [4]:
layer_number = 102
table = pq.read_table(f"{layer_table_folder}/{config_folder}/{layer_number}.parquet")

In [12]:
layer = table.to_pydict()

In [19]:
non_array = [str, int, float]
converted_layer = {}
for key, value in layer.items():
    layer_value = value[0]
    # print(key, type(layer_value))
    if (type(layer_value) in non_array):
        print(key, layer_value)
        converted_layer[key] = layer_value
    elif(isinstance(value, list) and "shape" not in key):
        shape = layer[f"{key}_shape"][0]
        flattened_array = np.array(layer_value)
        array = flattened_array.reshape(shape)
        print(array.shape)
        converted_layer[key] = array


folder_layer_range 101-110
part OverhangPart
part_section OVERHANG-05deg
process LPBFthermography
source NIST
supports wSup
layer_number 102
(3, 664)
contact_email jarred.heigel@nist.gov
file_name 20180801_OverhangStudy_Layer102.mat
hatch_spacing 100
laser_power 195
layer_thickness 20
material IN625
(664, 126, 360)
(1, 664)
(2, 1)
s_hvariable__a 2.655
s_hvariable__b -800.7
s_hvariable__c 1940000.0
scan_speed 800
website nist.gov/el/lpbf-thermography/3D-part-builds/OverhangPart-IN625


In [28]:
for key, value in converted_layer.items():
    print(key, type(value))
    if(isinstance(value, np.ndarray)):
        print(value.shape)


folder_layer_range <class 'str'>
part <class 'str'>
part_section <class 'str'>
process <class 'str'>
source <class 'str'>
supports <class 'str'>
layer_number <class 'int'>
build_time <class 'numpy.ndarray'>
(3, 664)
contact_email <class 'str'>
file_name <class 'str'>
hatch_spacing <class 'int'>
laser_power <class 'int'>
layer_thickness <class 'int'>
material <class 'str'>
radiant_temp <class 'numpy.ndarray'>
(664, 126, 360)
raw_frame_number <class 'numpy.ndarray'>
(1, 664)
resolution <class 'numpy.ndarray'>
(2, 1)
s_hvariable__a <class 'float'>
s_hvariable__b <class 'float'>
s_hvariable__c <class 'float'>
scan_speed <class 'int'>
website <class 'str'>


In [ ]:
print("called", table)
arrow_radiant_temps_flat = np.array(table["radiant_temp"][0].as_py())

In [ ]:
# arrow_radiant_temps_shape = [int(size) for size in table["radiant_temp_shape"][0]]
arrow_radiant_temps_shape = tuple(table["radiant_temp_shape"][0].as_py())
print(arrow_radiant_temps_shape)

In [ ]:
arrow_radiant_temps_reshaped = arrow_radiant_temps_flat.reshape(arrow_radiant_temps_shape)
print(arrow_radiant_temps_reshaped[100])
plt.imshow(arrow_radiant_temps_reshaped[100])
plt.show()

In [ ]:
for layer in layers:
    layer_number = layer["layer_number"]
    with open(f"{layers_folder}/{config_folder}/{layer_number}.pkl", "wb") as f:
        pickle.dump(layer, f)

In [ ]:
layers[0]

In [ ]:
layer_number = 1
with open(f"{layers_folder}/{config_folder}/{layer_number}.pkl", "rb") as f:
    layer = pickle.load(f)

print(layer)